In [15]:
import torch
from torchtrainer.models.resunet import ResUNet
from torchtrainer.inspector import Inspector
from torchtrainer.profiling import benchmark_model

# Dummy data. In a real application this should be a batch of the dataset.
batch = torch.rand(8, 1, 224, 224)
labels = torch.randint(0, 1000, (8,))

model = ResUNet((3, 3, 3), (16, 32, 64))
model.eval();

### Model inspection

In [12]:
# Check intermediate activations of the model, as well as gradients and parameters
insp = Inspector(model)
# For activations, we need to explicitly start tracking to set up the forward hooks.
insp.start_tracking_activations()

# Apply model to batch
res = model(batch)
# Dummy calculation of loss and gradients, just as an example.
loss = res.sum().backward()

# Remove the forward hooks
insp.stop_tracking_activations()

# Activations
acts = insp.get_activations()
# Parameters
params = insp.get_params()
# Gradients
grads = insp.get_grads()

print(acts)

{'resunet.conv1': tensor([[[[-2.1133e-02, -2.3763e-01, -8.5592e-03,  ...,  8.9696e-02,
            3.5621e-02, -3.2576e-02],
          [ 7.5440e-02, -2.3085e-01, -1.2498e-01,  ...,  8.7733e-02,
            1.0410e-01,  4.2927e-02],
          [ 1.4145e-01, -6.2567e-02,  8.0156e-02,  ...,  1.0289e-01,
            1.0193e-01,  2.2981e-02],
          ...,
          [-7.9730e-02,  2.5979e-02, -9.6675e-02,  ..., -8.1336e-02,
           -1.5699e-02, -4.5765e-03],
          [ 1.0428e-01, -3.6347e-02, -1.8489e-01,  ..., -1.4531e-01,
           -2.1231e-01, -1.3798e-01],
          [ 7.4693e-02, -3.0195e-02, -1.8662e-02,  ...,  4.6596e-03,
           -1.1774e-01, -2.3507e-01]],

         [[ 5.5460e-02,  4.4487e-02, -6.2034e-02,  ...,  3.6630e-02,
           -7.6633e-02,  3.4101e-02],
          [ 1.0550e-01,  1.7348e-02,  1.4353e-01,  ..., -3.4005e-02,
            1.3457e-01, -4.2032e-03],
          [-2.0062e-02,  9.5806e-02,  7.7992e-02,  ...,  7.0648e-02,
           -3.7849e-02, -5.8865e-04],
  

In [17]:
def agg_func(data, module_name, data_type):
    return torch.tensor([data.min(), data.max()])

# Tracking activations involves copying all the data from the GPU to the CPU (to preserve GPU memory), which
# is expensive. We can provide and aggregation function that will be applied to the data before copying
insp = Inspector(model, agg_func=agg_func)
insp.start_tracking_activations()
res = model(batch)
insp.stop_tracking_activations()

acts = insp.get_activations()
print(acts)

{'resunet.conv1': tensor([-0.6399,  0.6600]), 'resunet.bn1': tensor([-0.6399,  0.6600]), 'resunet.relu': tensor([0.0000, 0.6600]), 'resunet.encoder.stage_0.0.conv1': tensor([-0.7086,  0.6848]), 'resunet.encoder.stage_0.0.bn1': tensor([-0.7086,  0.6848]), 'resunet.encoder.stage_0.0.relu1': tensor([0.0000, 0.6848]), 'resunet.encoder.stage_0.0.conv2': tensor([-0.5015,  0.6012]), 'resunet.encoder.stage_0.0.bn2': tensor([-0.5015,  0.6012]), 'resunet.encoder.stage_0.0.relu2': tensor([0.0000, 1.2852]), 'resunet.encoder.stage_0.0.downsample.0': tensor([-0.7685,  1.0222]), 'resunet.encoder.stage_0.0.downsample.1': tensor([-0.7685,  1.0222]), 'resunet.encoder.stage_0.0.downsample': tensor([-0.7685,  1.0222]), 'resunet.encoder.stage_0.0': tensor([0.0000, 1.2852]), 'resunet.encoder.stage_0.1.conv1': tensor([-0.9120,  1.0681]), 'resunet.encoder.stage_0.1.bn1': tensor([-0.9120,  1.0681]), 'resunet.encoder.stage_0.1.relu1': tensor([0.0000, 1.0681]), 'resunet.encoder.stage_0.1.conv2': tensor([-0.9765,

### Model profiling

In [18]:
tensor_shape = (8, 1, 224, 224)
# Benchmark the model for training
stats_train = benchmark_model(model, tensor_shape, no_grad=False, call_backward=True, use_float16=True, return_model_info=True)
# Benchmark for inference
stats_val = benchmark_model(model, tensor_shape, no_grad=True, call_backward=False, use_float16=True, return_model_info=False)
# The units for each metric are also included in the dictionary
print(stats_train)
print(stats_val)

Unsupported operator aten::batch_norm encountered 47 time(s)
Unsupported operator aten::add_ encountered 19 time(s)
Unsupported operator aten::upsample_nearest2d encountered 3 time(s)
Unsupported operator aten::add_ encountered 19 time(s)


{'params': 0.450128, 'activations': 0.090116096, 'flops': 15.10699008, 'memory': 0.39917755126953125, 'time_cpu': 0.02100062370300293, 'time_gpu': 0.24994224548339844, 'info': ['params: M', 'activations: G', 'flops: G', 'memory: GiB', 'time_cpu: s', 'time_gpu: s']}
{'params': 0.0, 'activations': 0.0, 'flops': 0.0, 'memory': 0.15419673919677734, 'time_cpu': 0.008998870849609375, 'time_gpu': 0.009273183822631837, 'info': ['params: M', 'activations: G', 'flops: G', 'memory: GiB', 'time_cpu: s', 'time_gpu: s']}
